In [2]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.optim import AdamW
from torch.utils.data import Dataset, DataLoader
from tqdm.notebook import tqdm
from sklearn.metrics import precision_score, recall_score, f1_score

In [4]:
data_df = pd.read_csv('winequality-red.csv')

In [5]:
data_df.head()

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   
3           11.2              0.28         0.56             1.9      0.075   
4            7.4              0.70         0.00             1.9      0.076   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   
3                 17.0                  60.0   0.9980  3.16       0.58   
4                 11.0                  34.0   0.9978  3.51       0.56   

   alcohol  quality  
0      9.4        5  
1      9.8        5  
2      9.8        5  
3      9.8        6  
4      9.4        5

In [6]:
data_df.shape

(1599, 12)

In [7]:
# how many features?
len(data_df.columns) - 1

11

In [ ]:
data_df.quality.unique()

array([5, 6, 7, 4, 8, 3])

In [9]:
# convert these quaity measures to labels (0 to 5)
def get_label(quality):
    if quality == 3:
        return 0
    elif quality == 4:
        return 1
    elif quality == 5:
        return 2
    elif quality == 6:
        return 3
    elif quality == 7:
        return 4
    else:
        return 5

labels = data_df['quality'].apply(get_label)

# normalize data
data_df = (data_df - data_df.mean()) / data_df.std()
data_df['label'] = labels

In [10]:
data_df.head()

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0      -0.528194          0.961576    -1.391037       -0.453077  -0.243630   
1      -0.298454          1.966827    -1.391037        0.043403   0.223805   
2      -0.298454          1.296660    -1.185699       -0.169374   0.096323   
3       1.654339         -1.384011     1.483689       -0.453077  -0.264878   
4      -0.528194          0.961576    -1.391037       -0.453077  -0.243630   

   free sulfur dioxide  total sulfur dioxide   density        pH  sulphates  \
0            -0.466047             -0.379014  0.558100  1.288240  -0.579025   
1             0.872365              0.624168  0.028252 -0.719708   0.128910   
2            -0.083643              0.228975  0.134222 -0.331073  -0.048074   
3             0.107558              0.411372  0.664069 -0.978798  -0.461036   
4            -0.466047             -0.379014  0.558100  1.288240  -0.579025   

    alcohol   quality  label  
0 -0.959946 -0.787576      2  
1 -0.584594 -0.787576      2  
2 -0.584594 -0.787576      2  
3 -0.584594  0.450707      3  
4 -0.959946 -0.787576      2

In [11]:
# sumamry statistics of the data
data_df.describe()

fixed acidity  volatile acidity   citric acid  residual sugar  \
count   1.599000e+03      1.599000e+03  1.599000e+03    1.599000e+03   
mean    4.088176e-16      1.599721e-16 -8.887339e-17   -1.155354e-16   
std     1.000000e+00      1.000000e+00  1.000000e+00    1.000000e+00   
min    -2.136377e+00     -2.277567e+00 -1.391037e+00   -1.162333e+00   
25%    -7.004996e-01     -7.696903e-01 -9.290275e-01   -4.530767e-01   
50%    -2.410190e-01     -4.367545e-02 -5.634264e-02   -2.402999e-01   
75%     5.056370e-01      6.264921e-01  7.650078e-01    4.340257e-02   
max     4.353787e+00      5.876138e+00  3.742403e+00    9.192806e+00   

          chlorides  free sulfur dioxide  total sulfur dioxide       density  \
count  1.599000e+03         1.599000e+03          1.599000e+03  1.599000e+03   
mean   2.132961e-16        -4.443669e-17          3.554936e-17 -3.466062e-14   
std    1.000000e+00         1.000000e+00          1.000000e+00  1.000000e+00   
min   -1.603443e+00        -1.422055e+00         -1.230199e+00 -3.537625e+00   
25%   -3.711129e-01        -8.484502e-01         -7.438076e-01 -6.075656e-01   
50%   -1.798892e-01        -1.792441e-01         -2.574163e-01  1.759533e-03   
75%    5.382858e-02         4.899619e-01          4.721707e-01  5.766445e-01   
max    1.112355e+01         5.365606e+00          7.372847e+00  3.678904e+00   

                 pH     sulphates       alcohol       quality        label  
count  1.599000e+03  1.599000e+03  1.599000e+03  1.599000e+03  1599.000000  
mean   2.879498e-15  6.754377e-16  8.887339e-17  7.109871e-17     2.636023  
std    1.000000e+00  1.000000e+00  1.000000e+00  1.000000e+00     0.807569  
min   -3.699244e+00 -1.935902e+00 -1.898325e+00 -3.264143e+00     0.000000  
25%   -6.549356e-01 -6.380200e-01 -8.661079e-01 -7.875763e-01     2.000000  
50%   -7.210449e-03 -2.250577e-01 -2.092427e-01  4.507074e-01     3.000000  
75%    5.757422e-01  4.238832e-01  6.352984e-01  4.507074e-01     3.000000  
max    4.526866e+00  7.916200e+00  4.201138e+00  2.927275e+00     5.000000

In [12]:
# The dataset class
class WineDataset(Dataset):

    def __init__(self, data_df):
        self.data_df = data_df
        self.features = []
        self.labels = []
        for _, i in data_df.iterrows():
          self.features.append([i['fixed acidity'], i['volatile acidity'], i['citric acid'], i['residual sugar'], i['chlorides'], i['free sulfur dioxide'], i['total sulfur dioxide'], i['density'], i['pH'], i['sulphates'], i['alcohol']])
          self.labels.append(i['label'])

    def __len__(self):
        return len(self.data_df)

    def __getitem__(self, idx):
        if torch.is_tensor(idx):
            idx = idx.tolist()

        features = self.features[idx]
        features = torch.FloatTensor(features)

        labels = torch.tensor(self.labels[idx], dtype = torch.long)

        return {'labels': labels, 'features': features}

wine_dataset = WineDataset(data_df)
train_dataset, val_dataset, test_dataset = torch.utils.data.random_split(wine_dataset, [0.8, 0.1, 0.1])

# The dataloader
train_dataloader = DataLoader(train_dataset, batch_size = 4, shuffle = True, num_workers = 0)
val_dataloader = DataLoader(val_dataset, batch_size = 4, shuffle = False, num_workers = 0)
test_dataloader = DataLoader(test_dataset, batch_size = 4, shuffle = False, num_workers = 0)

In [13]:
# peak into the dataset
for i in wine_dataset:
  print(i)
  break

{'labels': tensor(2), 'features': tensor([-0.5282,  0.9616, -1.3910, -0.4531, -0.2436, -0.4660, -0.3790,  0.5581,
         1.2882, -0.5790, -0.9599])}


In [14]:
# change the device to gpu if available
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [15]:
class WineModel(torch.nn.Module):

    def __init__(self):
        super(WineModel, self).__init__()

        self.linear1 = torch.nn.Linear(11, 200)
        self.activation = torch.nn.ReLU()
        self.linear2 = torch.nn.Linear(200, 6)
        self.softmax = torch.nn.Softmax()

    def forward(self, x):
        x = self.linear1(x)
        x = self.activation(x)
        x = self.linear2(x)
        x = self.softmax(x)
        return x

winemodel1 = WineModel().to(device)

In [16]:
# Define and the loss function and optimizer
criterion = nn.CrossEntropyLoss().to(device)
optimizer = AdamW(winemodel1.parameters(), lr = 1e-3)

In [17]:
# Lets define the training steps
def accuracy(preds, labels):
    preds = torch.argmax(preds, dim=1).flatten()
    labels = labels.flatten()
    return torch.sum(preds == labels) / len(labels)

def train(model, data_loader, optimizer, criterion):
    epoch_loss = 0
    epoch_acc = 0
    model.train()
    
    for d in tqdm(data_loader):
    inputs = d['features'].to(device)
    labels = d['labels'].to(device)
    outputs = model(inputs)

    _, preds = torch.max(outputs, dim=1)
    loss = criterion(outputs, labels)
    acc = accuracy(outputs, labels)

    loss.backward()
    optimizer.step()
    optimizer.zero_grad()

    epoch_loss += loss.item()
    epoch_acc += acc.item()

    return epoch_loss / len(data_loader), epoch_acc / len(data_loader)

# Lets define the testing steps
def evaluate(model, data_loader, criterion):
    epoch_loss = 0
    epoch_acc = 0
    model.eval()
    with torch.no_grad():
        for d in data_loader:
            inputs = d['features'].to(device)
            labels = d['labels'].to(device)
            outputs = model(inputs)

            _, preds = torch.max(outputs, dim=1)
            loss = criterion(outputs, labels)
            acc = accuracy(outputs, labels)

            epoch_loss += loss.item()
            epoch_acc += acc.item()

    return epoch_loss / len(data_loader), epoch_acc / len(data_loader)

In [18]:
for epoch in range(100):
    train_loss, train_acc = train(winemodel1, train_dataloader, optimizer, criterion)
    valid_loss, valid_acc = evaluate(winemodel1, val_dataloader, criterion)

    print(f'| Epoch: {epoch+1:02} | Train Loss: {train_loss:.3f} | Train Acc: {train_acc*100:.2f}% | Val. Loss: {valid_loss:.3f} | Val. Acc: {valid_acc*100:.2f}% |')

  0%|          | 0/320 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1736: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  return self._call_impl(*args, **kwargs)


| Epoch: 01 | Train Loss: 1.532 | Train Acc: 54.84% | Val. Loss: 1.472 | Val. Acc: 57.50% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 02 | Train Loss: 1.461 | Train Acc: 59.53% | Val. Loss: 1.463 | Val. Acc: 58.13% |


...

| Epoch: 98 | Train Loss: 1.305 | Train Acc: 75.31% | Val. Loss: 1.400 | Val. Acc: 65.00% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 99 | Train Loss: 1.302 | Train Acc: 75.08% | Val. Loss: 1.414 | Val. Acc: 62.50% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 100 | Train Loss: 1.301 | Train Acc: 75.31% | Val. Loss: 1.406 | Val. Acc: 63.75% |


In [19]:
test_loss_1, test_acc_1 = evaluate(winemodel1, test_dataloader, criterion)
print(f'| Test Loss: {test_loss_1:.3f} | Test Acc: {test_acc_1*100:.2f}% |')

all_preds = []
all_labels = []
winemodel1.eval()
with torch.no_grad():
    for batch in test_dataloader:
        inputs, labels = batch['features'],batch['labels']
        inputs, labels = inputs.to(device), labels.to(device)
        outputs = winemodel1(inputs)
        preds = torch.argmax(outputs, dim=1)  # Get predicted class
        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())
all_preds = np.array(all_preds)
all_labels = np.array(all_labels)
precision = precision_score(all_labels, all_preds, average='weighted')
recall = recall_score(all_labels, all_preds, average='weighted')
f1 = f1_score(all_labels, all_preds, average='weighted')
print(f'Precision: {precision:.4f}')
print(f'Recall: {recall:.4f}')
print(f'F1 Score: {f1:.4f}')

| Test Loss: 1.456 | Test Acc: 59.58% |
Precision: 0.5697
Recall: 0.5975
F1 Score: 0.5813


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


**Key Insights**:

- After evaluating the model on the test set, we observed that test accuracy (59.58%) was lower than validation accuracy (63.75%) and significantly lower than training accuracy (75.31%).
- This suggests that the model is overfitting, as it performs well on the training data but struggles to generalize on the test data.

### Hyper Parameter Tuning

In [20]:
winemodel2 = WineModel().to(device)
optimizer = AdamW(winemodel2.parameters(), lr = 1.2e-3) # Increased learning rate

for epoch in range(150): # Increased number of epochs
    train_loss, train_acc = train(winemodel2, train_dataloader, optimizer, criterion)
    valid_loss, valid_acc = evaluate(winemodel2, val_dataloader, criterion)
    print(f'| Epoch: {epoch+1:02} | Train Loss: {train_loss:.3f} | Train Acc: {train_acc*100:.2f}% | Val. Loss: {valid_loss:.3f} | Val. Acc: {valid_acc*100:.2f}% |')
test_loss_2, test_acc_2 = evaluate(winemodel2, test_dataloader, criterion)
print(f'| Test Loss: {test_loss_2:.3f} | Test Acc: {test_acc_2*100:.2f}% |')
all_preds = []
all_labels = []
winemodel2.eval()
with torch.no_grad():
    for batch in test_dataloader:
        inputs, labels = batch['features'],batch['labels']
        inputs, labels = inputs.to(device), labels.to(device)
        outputs = winemodel2(inputs)
        preds = torch.argmax(outputs, dim=1)  # Get predicted class
        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())
all_preds = np.array(all_preds)
all_labels = np.array(all_labels)
precision = precision_score(all_labels, all_preds, average='weighted')
recall = recall_score(all_labels, all_preds, average='weighted')
f1 = f1_score(all_labels, all_preds, average='weighted')
print(f'Precision: {precision:.4f}')
print(f'Recall: {recall:.4f}')
print(f'F1 Score: {f1:.4f}')

  0%|          | 0/320 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1736: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  return self._call_impl(*args, **kwargs)


| Epoch: 01 | Train Loss: 1.525 | Train Acc: 53.44% | Val. Loss: 1.471 | Val. Acc: 56.88% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 02 | Train Loss: 1.460 | Train Acc: 59.38% | Val. Loss: 1.465 | Val. Acc: 56.88% |


...

  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 149 | Train Loss: 1.272 | Train Acc: 78.28% | Val. Loss: 1.393 | Val. Acc: 65.62% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 150 | Train Loss: 1.270 | Train Acc: 78.05% | Val. Loss: 1.403 | Val. Acc: 65.62% |
| Test Loss: 1.440 | Test Acc: 62.08% |
Precision: 0.5888
Recall: 0.6226
F1 Score: 0.6052


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


**Changes made in model layers**:
- Increased epochs from 100 to 150.
- Increased learning rate from 1e-3 to 1.2e-3.

**Key Insights**:
- Test Accuracy increased from 59.58% → 62.08%.
- Overfitting is reduced slightly as train and test accuracy remain close.
- However, the gap between training accuracy (78.05%) and test accuracy (62.08%) suggests overfitting, meaning the model is learning patterns that do not generalize well to unseen data.

In [21]:
# Updated Model Definition
class WineModelDnn(torch.nn.Module):
    def __init__(self):
        super(WineModelDnn, self).__init__()
        self.linear1 = torch.nn.Linear(11, 200)
        self.activation1 = torch.nn.ReLU()
        self.linear2 = torch.nn.Linear(200, 100)  # Added a new hidden layer
        self.activation2 = torch.nn.ReLU()
        self.linear3 = torch.nn.Linear(100, 6)
        self.softmax = torch.nn.Softmax()

    def forward(self, x):
        x = self.linear1(x)
        x = self.activation1(x)
        x = self.linear2(x) # Forward pass through the new hidden layer
        x = self.activation2(x)
        x = self.linear3(x)
        x = self.softmax(x)
        return x

winemodel3 = WineModelDnn().to(device)

# Re-initialize optimizer with the new model parameters
optimizer = AdamW(winemodel3.parameters(), lr = 1.2e-3)

# Re-train the model with increased depth
for epoch in range(150):
    train_loss, train_acc = train(winemodel3, train_dataloader, optimizer, criterion)
    valid_loss, valid_acc = evaluate(winemodel3, val_dataloader, criterion)
    print(f'| Epoch: {epoch+1:02} | Train Loss: {train_loss:.3f} | Train Acc: {train_acc*100:.2f}% | Val. Loss: {valid_loss:.3f} | Val. Acc: {valid_acc*100:.2f}% |')

test_loss_3, test_acc_3 = evaluate(winemodel3, test_dataloader, criterion)
print(f'| Test Loss: {test_loss_3:.3f} | Test Acc: {test_acc_3*100:.2f}% |')
all_preds = []
all_labels = []
winemodel3.eval()
with torch.no_grad():
    for batch in test_dataloader:
        inputs, labels = batch['features'],batch['labels']
        inputs, labels = inputs.to(device), labels.to(device)
        outputs = winemodel3(inputs)
        preds = torch.argmax(outputs, dim=1)  # Get predicted class
        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())
all_preds = np.array(all_preds)
all_labels = np.array(all_labels)
precision = precision_score(all_labels, all_preds, average='weighted')
recall = recall_score(all_labels, all_preds, average='weighted')
f1 = f1_score(all_labels, all_preds, average='weighted')
print(f'Precision: {precision:.4f}')
print(f'Recall: {recall:.4f}')
print(f'F1 Score: {f1:.4f}')

  0%|          | 0/320 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1736: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  return self._call_impl(*args, **kwargs)


| Epoch: 01 | Train Loss: 1.497 | Train Acc: 55.31% | Val. Loss: 1.462 | Val. Acc: 57.50% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 02 | Train Loss: 1.446 | Train Acc: 60.08% | Val. Loss: 1.459 | Val. Acc: 56.88% |


...

  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 149 | Train Loss: 1.352 | Train Acc: 69.14% | Val. Loss: 1.431 | Val. Acc: 61.25% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 150 | Train Loss: 1.352 | Train Acc: 69.14% | Val. Loss: 1.433 | Val. Acc: 61.25% |
| Test Loss: 1.417 | Test Acc: 62.71% |
Precision: 0.5573
Recall: 0.6289
F1 Score: 0.5839


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


**Changes Made in Model Layers**:

- Added one more hidden layer.
- Structure changed from 1 hidden layer → 2 hidden layers.
- Kept the same number of epochs and learning rate from earlier enhancement.

**Key Insights**:

- Adding an additional hidden layer reduced training accuracy (69.14%), but the test accuracy slightly increased to 62.71%.
- The gap between training and test accuracy became smaller, indicating a reduction in overfitting.
- However, the decrease in training accuracy suggests the model may be struggling to learn the data efficiently due to complexity or insufficient training time.


In [37]:

# Updated Model Definition
class WineModelDnnExpanded(torch.nn.Module):
    def __init__(self):
        super(WineModelDnnExpanded, self).__init__()
        self.linear1 = torch.nn.Linear(11, 300)  # Increased neurons to 256
        self.activation1 = torch.nn.ReLU()
        self.linear2 = torch.nn.Linear(300, 150)  # Increased neurons to 128
        self.activation2 = torch.nn.ReLU()
        self.linear3 = torch.nn.Linear(150, 6)
        self.softmax = torch.nn.Softmax()

    def forward(self, x):
        x = self.linear1(x)
        x = self.activation1(x)
        x = self.linear2(x)
        x = self.activation2(x)
        x = self.linear3(x)
        x = self.softmax(x)
        return x

winemodel4 = WineModelDnnExpanded().to(device)

optimizer = AdamW(winemodel4.parameters(), lr = 1.2e-3)

patience = 10
best_val_loss = np.inf
epochs_no_improve = 0
for epoch in range(150):
    train_loss, train_acc = train(winemodel4, train_dataloader, optimizer, criterion)
    valid_loss, valid_acc = evaluate(winemodel4, val_dataloader, criterion)

    print(f'| Epoch: {epoch+1:02} | Train Loss: {train_loss:.3f} | Train Acc: {train_acc*100:.2f}% | Val. Loss: {valid_loss:.3f} | Val. Acc: {valid_acc*100:.2f}% |')
test_loss_4, test_acc_4 = evaluate(winemodel4, test_dataloader, criterion)
print(f'| Test Loss: {test_loss_4:.3f} | Test Acc: {test_acc_4*100:.2f}% |')
all_preds = []
all_labels = []
winemodel4.eval()
with torch.no_grad():
    for batch in test_dataloader:
        inputs, labels = batch['features'],batch['labels']
        inputs, labels = inputs.to(device), labels.to(device)
        outputs = winemodel4(inputs)
        preds = torch.argmax(outputs, dim=1)
        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())
all_preds = np.array(all_preds)
all_labels = np.array(all_labels)
precision = precision_score(all_labels, all_preds, average='weighted')
recall = recall_score(all_labels, all_preds, average='weighted')
f1 = f1_score(all_labels, all_preds, average='weighted')
print(f'Precision: {precision:.4f}')
print(f'Recall: {recall:.4f}')
print(f'F1 Score: {f1:.4f}')

  0%|          | 0/320 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1736: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  return self._call_impl(*args, **kwargs)


| Epoch: 01 | Train Loss: 1.488 | Train Acc: 55.94% | Val. Loss: 1.472 | Val. Acc: 56.25% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 02 | Train Loss: 1.448 | Train Acc: 59.22% | Val. Loss: 1.462 | Val. Acc: 58.13% |


...

  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 149 | Train Loss: 1.328 | Train Acc: 71.64% | Val. Loss: 1.432 | Val. Acc: 60.62% |


  0%|          | 0/320 [00:00<?, ?it/s]

| Epoch: 150 | Train Loss: 1.325 | Train Acc: 71.88% | Val. Loss: 1.418 | Val. Acc: 63.12% |
| Test Loss: 1.413 | Test Acc: 63.33% |
Precision: 0.6163
Recall: 0.6352
F1 Score: 0.6037


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


**Updates to the Model layers**:
- Increased the number of neurons in each layer (layer 1: 200 -> 300, layer 2: 100 -> 150) with same number of hidden layers, learning rate, epochs as earlier.

**Key Insights**:
- Train Accuracy increased from 69.14% to 71.88%, suggesting the wider model is better at fitting the training data.
- Test Accuracy increased from 62.71% to 63.33%, indicating improved generalization.
- F1 Score also improved (from 0.5839 to 0.6037), confirming the model is better at balancing precision and recall.
